In [ ]:
!pip install selenium
!pip install webdriver_manager
!pip install --upgrade webdriver_manager

In [2]:
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.action_chains import ActionChains
from webdriver_manager.chrome import ChromeDriverManager
import requests
import pandas as pd
import numpy as np
import csv
import time
from selenium import webdriver
from selenium.webdriver.firefox.service import Service
from webdriver_manager.firefox import GeckoDriverManager
from selenium.webdriver.firefox.options import Options
from webdriver_manager.microsoft import EdgeChromiumDriverManager
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC


# This is my first crawling file after a long time, so it's going to be messy

# Crawling and saving links as a savepoint

In [ ]:
NBC_NEWS_POLITICS = 'https://www.nbcnews.com/politics'
NBC_NEWS_HEALTH = 'https://www.nbcnews.com/health'
NBC_NEWS_BUSINESS = 'https://www.nbcnews.com/business'
NBC_NEWS_SPORTS = 'https://www.nbcnews.com/news/sports'
NBC_NEWS_SCIENCE = 'https://www.nbcnews.com/science'

NBC_NEWS_ORIGINAL = 'https://www.nbcnews.com/'

ALL_CLASSES_LINK = [NBC_NEWS_POLITICS, NBC_NEWS_HEALTH, NBC_NEWS_BUSINESS, NBC_NEWS_SPORTS, NBC_NEWS_SCIENCE]

options = Options()
options.add_argument("--headless")  # Ensure GUI is off

webdriver_service = Service(GeckoDriverManager().install())
driver = webdriver.Firefox(service=webdriver_service, options=options)


all_link = []

for class_link in ALL_CLASSES_LINK:
  driver.get(class_link)

  time.sleep(10)

  BUTTON_PRESS_TIMES = 100
  NUMBER_OF_JOBS = BUTTON_PRESS_TIMES * 20 + 10

  FIND_MORE_BUTTON_CSS_CLASS = '.animated-ghost-button.animated-ghost-button--normal.styles_button__khb8K'
  FIND_MORE_BUTTON_XPATH = '//button[@data-testid="button-hover-animation"]'
  
  for i in range(BUTTON_PRESS_TIMES):
      print(f"Iteration number {i}")
      try:
        load_more_button = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.XPATH, FIND_MORE_BUTTON_XPATH)))
        
        load_more_button.click()
        time.sleep(5)
      except Exception as e:
          print("Something went wrong pressing the button")
          break

  html_content = driver.page_source
  soup = BeautifulSoup(html_content, 'html.parser')

  # Lưu tất cả các link của job offer
  elements = driver.find_elements("xpath", '//a[h2[@class="wide-tease-item__headline"]]')
  links = [element.get_attribute('href') for element in elements]
  all_link.append(links)

  for link in links:
    print(link)

print("captured a total of ", len(all_link), " links")


In [4]:
driver.close()

In [5]:
for links in all_link:
    print(len(links))

150
150
150
150
150


## Saving

In [6]:
transposed_data = list(map(list, zip(*all_link)))

csv_filename = 'nbc_news.csv'

with open(csv_filename, 'w', newline='', encoding='utf-8') as csvfile:
    csv_writer = csv.writer(csvfile)

    csv_writer.writerow(["politics", "health", "business", "sports", "science"])

    csv_writer.writerows(transposed_data)

print(f"Data extracted and saved to '{csv_filename}'")

# Getting content from links

In [17]:
driver = webdriver.Firefox(service=webdriver_service, options=options)

categories = ['politics', 'health', 'business', 'sports', 'science']
for i in range (len(all_link)):
    data = []
    CSV_SAVE_NAME = categories[i] + '_nbc_news.csv'
    with open(CSV_SAVE_NAME, 'w', newline='', encoding='utf-8') as csvfile:
        csv_writer = csv.writer(csvfile)
        csv_writer.writerow(["title", "content", "category", "link"])
        for link in (all_link[i]):
            print(link)
            
            title = ''
            content = ''
            
            TITLE_CLASS = "article-hero-headline__htag lh-none-print black-print"
            CONTENT_CLASS = "article-body__content"
            
            driver.get(link)
            html_content = driver.page_source
            soup = BeautifulSoup(html_content, 'html.parser')
            
            titles = soup.find_all('h1', class_= TITLE_CLASS)
            contents = soup.find_all('div', class_= CONTENT_CLASS)
            
            if title is not None:
                title = [element.text.strip() for element in titles]
                title = ' '.join(title)
            if content is not None:
                content = [element.text.strip() for element in contents]
                content = ' '.join(content)
            print(title, content)
            data.append([title, content, categories[i], link])
        csv_writer.writerows(data)
    

https://www.nbcnews.com/politics/supreme-court/supreme-court-homelessness-grants-pass-rcna142977
How a small city in Oregon could shape the way major U.S. cities handle homelessness GRANTS PASS, Ore. — For more than five years, Helen Cruz lived on the streets of Grants Pass.A small, rural town of roughly 40,000 people, the city has now found itself at the center of a homeless crisis plaguing major cities across the U.S.“We’re in this situation not because we want to be. We’re in this situation because we don’t have a choice right now,” Cruz, 49, said in an interview.For years, Grants Pass has been embroiled in a contentious lawsuit with homeless residents like Cruz, who argue that anti-camping ordinances enacted by the city — including fines for sleeping in any park or public space — violate their constitutional rights.Helen Cruz in Grant Pass, Ore.Dan Dvorak / NBC NewsThe legal battle has now gone all the way to the U.S. Supreme Court, which is scheduled to hear arguments in the case 

In [18]:
driver.close()

In [21]:
lmao = pd.read_csv('./sports_nbc_news.csv')
lmao.head(10)

title  \
0  Lakers say typos on Kobe Bryant statue outside...   
1  Kirk Cousins to Atlanta, Saquon Barkley to Phi...   
2  MLB sees slowly improving diversity in its you...   
3  Timberwolves’ Rudy Gobert fined $100,000 for d...   
4  Temple University reviewing reports of potenti...   
5  Glistening buildings, crisp bed sheets and sec...   
6  Brittany Mahomes says her back is fractured an...   
7  Patrick Mahomes' younger brother sentenced in ...   
8  Some attendees of frigid Chiefs game forced in...   
9  Christian Horner calls on F1 to 'look forward'...   

                                             content category  \
0  The Los Angeles Lakers said Monday that spelli...   sports   
1  Kirk Cousins and Saquon Barkley, two of pro fo...   sports   
2  For much of Lee Allen Jr.’s childhood, basebal...   sports   
3  The NBA fined Minnesota center Rudy Gobert $10...   sports   
4  Temple University said it was looking into rep...   sports   
5  SAINT-DENIS, France — The beds for 10,000 Olym...   sports   
6  Brittany Mahomes revealed Wednesday that she f...   sports   
7  KANSAS CITY, Kan. — The younger brother of Sup...   sports   
8  At least "some" football fans, who attended Ja...   sports   
9  Red Bull team principal Christian Horner calle...   sports   

                                                link  
0  https://www.nbcnews.com/news/us-news/lakers-sa...  
1  https://www.nbcnews.com/news/us-news/kirk-cous...  
2  https://www.nbcnews.com/news/us-news/mlb-sees-...  
3  https://www.nbcnews.com/news/sports/timberwolv...  
4  https://www.nbcnews.com/business/business-news...  
5  https://www.nbcnews.com/news/world/glistening-...  
6  https://www.nbcnews.com/news/sports/brittany-m...  
7  https://www.nbcnews.com/news/us-news/patrick-m...  
8  https://www.nbcnews.com/news/us-news/attendees...  
9  https://www.nbcnews.com/news/sports/christian-...